In [ ]:
from bidict import bidict
import numpy as np
from time import time
from traceback import format_exc
import codecs
from scipy.sparse import csr_matrix
from math import floor

class CRSGraph(object):
    """ A graph based on the CSR sparse matrix data structure. """

    def __init__(self, neighbors_fpath):
        self._graph, self.index = self._load(neighbors_fpath) 
      
    
    def _get_or_add(self, dictionary, value):
        """ Gets the key associated with the value if exists. 
        Otherwiese inserts the value eq. to the length of the 
        dictionary and returns the key. """

        if value not in dictionary:
            value_idx = len(dictionary)
            dictionary[value] = len(dictionary)
        else:
            value_idx = dictionary[value]

        return value_idx

    
    def _load(self, neighbors_fpath):   
        tic = time()
        with codecs.open(neighbors_fpath, "r", "utf-8") as graph:
            src_lst = []
            dst_lst = []
            data_lst = []
            index = bidict()
            word_dict = {}
            for i, line in enumerate(graph):                
                if i % 10000000 == 0 and i != 0: print(i)
                try:
                    src, dst, weight = line.split("\t")
                    src = src.strip()
                    dst = dst.strip()
                    src_idx = self._get_or_add(index, src)
                    dst_idx = self._get_or_add(index, dst) 

                    src_lst.append(int(src_idx))
                    dst_lst.append(int(dst_idx))
                    data_lst.append(np.int16(floor(float(weight) * 10000.)))
                except:
                    print(format_exc())
                    print("Bad line:", line)

        rows = np.array(src_lst)
        cols = np.array(dst_lst)
        data = np.array(data_lst, dtype=np.int16)
        graph = csr_matrix( (data, (rows, cols)), shape=(len(index),len(index)), dtype=np.int16 )       
        print("Loaded in {:f} sec.".format(time() - tic))

        return graph, index 

    def get_neighbors(self, word):
        idx_i = self.index[word]
        
        nns = {self.index.inv[idx_j]: self._graph[idx_i].data[j] 
               for j, idx_j in enumerate(self._graph[idx_i].indices)}
        
        return nns
       
    def get_weight(self, word_i, word_j):
        return 0.0

    

from itertools import zip_longest
import argparse, sys, subprocess
from utils.common import exists
from os.path import basename
import gensim
import gzip
from gensim.models.keyedvectors import KeyedVectors
from gensim.utils import tokenize
from gensim.models.phrases import Phrases, Phraser
from gensim.models import Word2Vec
from time import time
import numpy as np
from chinese_whispers import chinese_whispers, aggregate_clusters
import codecs
import networkx as nx
from multiprocessing import Pool
from os.path import join
from collections import defaultdict
import codecs 
from time import time

import filter_clusters
import vector_representations.build_sense_vectors
from utils.common import ensure_dir
import pcz

verbose = True


def get_ego_network(ego):
    tic = time()
    ego_network = nx.Graph(name=ego)
    
    # Add related and substring nodes
    substring_nodes = []
    for j, node in enumerate(G.index):
        if ego.lower() == node.lower():
            nns_node = G.get_neighbors(node)
            ego_nodes = [(rn, {"weight": w}) for rn, w in nns_node.items()]
            ego_network.add_nodes_from(ego_nodes)
        else:
            if "_" not in node: continue
            if node.startswith(ego + "_") or node.endswith("_" + ego):
                substring_nodes.append( (node, {"weight": 9999}) )
    ego_network.add_nodes_from(substring_nodes)

    # Find edges of the ego network
    for r_node in ego_network:
        related_related_nodes = G.get_neighbors(r_node)
        related_related_nodes_ego = sorted(
            [(related_related_nodes[rr_node], rr_node) for rr_node in related_related_nodes if rr_node in ego_network],
            reverse=True)[:n]
        related_edges = [(r_node, rr_node, {"weight": w}) for w, rr_node in  related_related_nodes_ego]
        ego_network.add_edges_from(related_edges)

    chinese_whispers(ego_network, weighting="top", iterations=20)
    if verbose: print("{}\t{:f} sec.".format(ego, time()-tic))

    return ego_network


G = None
n = None


def ego_network_clustering(neighbors_fpath, clusters_fpath, max_related=300, num_cores=32):
    global G
    global n
    G = graph 
    
    with codecs.open(clusters_fpath, "w", "utf-8") as output, Pool(num_cores) as pool:
        output.write("word\tcid\tcluster\tisas\n")

        for i, ego_network in enumerate(pool.imap_unordered(get_ego_network, G.index)):
            if i % 100 == 0: print(i, "ego networks processed")
            sense_num = 1
            for label, cluster in sorted(aggregate_clusters(ego_network).items(), key=lambda e: len(e[1]), reverse=True):
                output.write("{}\t{}\t{}\t\n".format(
                    ego_network.name,
                    sense_num,
                    ", ".join( ["{}:{:.4f}".format(c_node, ego_network.node[c_node]["weight"]) for c_node in cluster] )
                ))
                sense_num += 1
    print("Clusters:", clusters_fpath)
           
        

neighbors_fpath = "model/wikipedia.txt.graph"
graph = CRSGraph(neighbors_fpath)
clusters_fpath = "model/tmp-wikipedia.txt"
ego_network_clustering(neighbors_fpath, clusters_fpath, max_related=300, num_cores=40)


10000000
20000000
30000000
40000000
50000000
60000000
70000000
80000000
90000000
100000000
110000000
120000000
130000000
140000000
150000000
160000000
170000000
180000000
190000000
200000000
210000000
220000000
230000000
240000000
250000000
260000000
270000000
280000000
290000000
300000000
310000000
320000000
330000000
340000000
350000000
360000000
370000000
380000000
390000000
400000000
Loaded in 3235.375555 sec.
directly	14.094615 sec.
0 ego networks processed
effectively	15.206112 sec.
proper	15.623029 sec.
a	15.711211 sec.
s	16.333110 sec.
however	17.639872 sec.
that	19.146779 sec.
thus	19.875358 sec.
them	20.049243 sec.
control	21.236644 sec.
every	21.726159 sec.
normal	22.034926 sec.
balance	22.146606 sec.
full	22.381471 sec.
only	22.477562 sec.
each	22.712250 sec.
their	23.140656 sec.
power	23.153863 sec.
continuous	23.707434 sec.
any	24.087077 sec.
whole	24.360562 sec.
an	24.803237 sec.
itself	25.170059 sec.
entire	25.414031 sec.
for	26.356250 sec.
his	26.402091 sec.
to	27.1855

whereas	19.793862 sec.
Although	9.108770 sec.
who	20.999694 sec.
but	22.122927 sec.
continental	23.295928 sec.
local	26.688418 sec.
foreign	24.581782 sec.
where	26.035109 sec.
by	18.930574 sec.
continually	16.172218 sec.
Meanwhile	14.568192 sec.
They	27.999861 sec.
Therefore	18.440588 sec.
physically	14.463442 sec.
or	25.747793 sec.
solid	35.705558 sec.
body	24.095203 sec.
Instead	22.706931 sec.
surfaces	16.407211 sec.
If	23.249314 sec.
already	14.848412 sec.
Furthermore	16.034491 sec.
hands	25.732754 sec.
But	15.006021 sec.
two	18.288681 sec.
own	22.828288 sec.
In	25.152347 sec.
chains	18.048296 sec.
barriers	16.170145 sec.
self	22.750607 sec.
Many	20.098462 sec.
pockets	12.235446 sec.
relationships	23.369554 sec.
if	24.502404 sec.
interactions	25.604202 sec.
Such	21.372445 sec.
always	20.614842 sec.
craft	22.167351 sec.
Finally	23.369745 sec.
For_example	7.947616 sec.
Some	22.947148 sec.
bodies	23.461658 sec.
interaction	23.871006 sec.
so	28.968984 sec.
as	33.284430 sec.
food	24.4517

wasn_t	14.203055 sec.
wire	24.430234 sec.
beam	27.432510 sec.
glasses	17.021231 sec.
remained	13.330893 sec.
machine	27.352621 sec.
molecules	18.797737 sec.
700 ego networks processed
clear	23.785915 sec.
Luis_Urzúa	9.083028 sec.
becomes	16.054986 sec.
heart	26.957589 sec.
angle	24.450709 sec.
stick	21.799242 sec.
noise	27.565996 sec.
was	22.560905 sec.
ultimate	25.714447 sec.
seemed	13.603777 sec.
became	22.691464 sec.
artillery_barrage	8.898009 sec.
newly	13.381113 sec.
orchidaceous	7.749994 sec.
Maghriban	8.247991 sec.
North_Koreans	9.322005 sec.
were	22.542008 sec.
isn_t	15.487673 sec.
had	23.732040 sec.
daylight	15.254663 sec.
arose	13.292866 sec.
albeit	12.824524 sec.
red	33.729916 sec.
Kamratmästerskapen	9.375519 sec.
remains	25.405798 sec.
gets	24.301090 sec.
Soviets	17.161588 sec.
Ottomans	16.493350 sec.
has	24.959290 sec.
Microbial_degradation	15.228462 sec.
got	23.917132 sec.
Plukenet	7.819731 sec.
saw	23.915597 sec.
Der_Hexenkreis	7.892289 sec.
Byzantines	16.386072 sec.
cam

forms	22.933479 sec.
reduces	16.169565 sec.
grows	18.511002 sec.
maintains	15.681519 sec.
bears	20.645267 sec.
appears	15.071846 sec.
supports	15.899834 sec.
displaces	8.367686 sec.
implies	23.462555 sec.
carries	14.679480 sec.
refers	14.381864 sec.
separator	16.489812 sec.
stays	15.611687 sec.
preserves	13.584631 sec.
inversion	17.009090 sec.
presents	23.639880 sec.
dominates	14.257302 sec.
fits	30.878207 sec.
feels	26.619556 sec.
utilizes	15.655411 sec.
organism	15.950469 sec.
distinguishes	15.016515 sec.
speck	13.099188 sec.
signifies	14.969068 sec.
falls	23.457160 sec.
clumping	15.624473 sec.
gives	19.450806 sec.
hourglass	13.865683 sec.
eliminates	15.065644 sec.
outer_layer	8.917642 sec.
poses	15.190870 sec.
rests	16.394221 sec.
takes	25.962543 sec.
holds	21.605673 sec.
depicts	16.918689 sec.
indentation	14.841700 sec.
originates	17.737007 sec.
emits	27.634786 sec.
stabilizes	18.159673 sec.
exceeds	15.435822 sec.
sees	24.944605 sec.
extends	14.279396 sec.
overshoot	13.849195 sec.


wise	23.323692 sec.
someone_else	15.452204 sec.
deformed	15.549243 sec.
visibly	14.006521 sec.
deliberate	15.876092 sec.
sensible	16.571798 sec.
excessively	14.268078 sec.
emotional	20.327584 sec.
sinister	16.418567 sec.
painful	15.537521 sec.
disturbing	16.211027 sec.
vindictive	13.521441 sec.
persuasion	14.670973 sec.
cynical	17.586099 sec.
repulsive	14.042016 sec.
unnatural	15.689784 sec.
clever	24.446045 sec.
gains	17.979030 sec.
charisma	17.509764 sec.
lean	24.010432 sec.
calm	23.809805 sec.
callous	15.504716 sec.
awkward	14.507479 sec.
jealous	17.188128 sec.
compassion	16.072642 sec.
flattery	15.907168 sec.
submissive	13.606354 sec.
scheming	16.129967 sec.
1400 ego networks processed
shame	24.146141 sec.
antagonistic	13.457799 sec.
deceptive	16.059461 sec.
ego	27.681032 sec.
anyway	21.853795 sec.
firmly	14.479003 sec.
frail	15.617800 sec.
crying	14.053654 sec.
biting	15.632142 sec.
nervous	23.690533 sec.
ineffectual	13.825305 sec.
convincing	14.175115 sec.
creative	22.860106 sec.

...

drypoint	13.929151 sec.
Civilian_Conservation	7.258835 sec.
proofreading	15.519737 sec.
toner	14.679794 sec.
flexographic	15.455174 sec.
regroups	8.858323 sec.
toner_cartridges	9.678285 sec.
vertebral_column	19.194691 sec.
knitting	15.826870 sec.
cyanotype	15.372990 sec.
Pop_Wuj	7.317255 sec.
movable_type	19.837439 sec.
enamelling	13.549785 sec.
xerography	17.316417 sec.
AmeriCorps_VISTA	8.937336 sec.
Volunteer_Ambulance	10.443070 sec.
ORMO	7.062953 sec.
phototypesetting	15.554379 sec.
compositors	14.552232 sec.
Gutenberg	14.772774 sec.
Cub_Scout	11.996898 sec.
Americorps	12.172595 sec.
electrotyping	16.366588 sec.
litho	16.082985 sec.
Lützow_Free	8.640605 sec.
unionised	6.708906 sec.
Boy_Scouts	9.149771 sec.
Liouville	6.651502 sec.
calico	19.419292 sec.
Riemann	7.628566 sec.
Fermat	8.724069 sec.
sapper	15.369698 sec.
decomposition_theorem	8.494443 sec.
embedding_theorem	8.751361 sec.
black_ops	10.513369 sec.
Weyl	8.962783 sec.
ZFC	6.690748 sec.
aeromedical	12.907014 sec.
Nullstellensa

Accelerator_Laboratory	8.188346 sec.
Geophysical_Fluid	13.379206 sec.
Heavy_Ion	7.290010 sec.
mint	27.898854 sec.
Neuropsychiatric_Institute	8.062928 sec.
USAMRIID	9.161526 sec.
SSRL	8.931497 sec.
lira	23.349172 sec.
Shockley_Semiconductor	9.370063 sec.
commemorative_coin	20.647719 sec.
NOAA_Geophysical	8.905014 sec.
Harwell	8.248263 sec.
Robotics_Lab	7.558503 sec.
Laboratory_ORNL	7.528817 sec.
Laboratory_LLNL	9.177501 sec.
Laboratory_RAL	8.892899 sec.
Fort_Detrick	8.416547 sec.
Guggenheim_Aeronautical	7.296853 sec.
Demonstrator	14.429885 sec.
Cetus_Corporation	9.000862 sec.
Laboratory_LANL	10.022002 sec.
Observatories	16.702833 sec.
Woods_Hole	8.957164 sec.
Biocontainment	15.403344 sec.
BBN_Technologies	7.095669 sec.
DSIR	7.222374 sec.
GALCIT	7.741917 sec.
Rothamsted_Research	8.871399 sec.
Proudman_Oceanographic	7.649748 sec.
Reactor	13.564492 sec.
Laboratory_MSL	7.200111 sec.
Lunar_Receiving	7.266771 sec.
KAPL	7.848892 sec.
HP_Labs	9.339535 sec.
MERL	16.606291 sec.
Laboratory_ANL	8.7

powdered_graphite	6.942618 sec.
Spike_Stent	8.340323 sec.
Ben_Grosse	9.795907 sec.
Jacknife_Lee	9.277287 sec.
Lord_Alge	6.608898 sec.
Andy_Sneap	7.881734 sec.
Randy_Staub	9.038384 sec.
Engineered	13.691638 sec.
centrifuging	9.653575 sec.
Humberto_Gatica	9.189565 sec.
phasing	14.327549 sec.
TN	22.307688 sec.
preponderantly	7.067566 sec.
scratching	15.077734 sec.
sizeable_minority	6.935706 sec.
Cenzo_Townshend	9.029375 sec.
Tom_Elmhirst	10.478518 sec.
mixing_mastering	15.371550 sec.
reverbs	14.873038 sec.
calcination	11.536859 sec.
predominantely	8.379794 sec.
shredding	14.997351 sec.
Oakwell	6.972737 sec.
muting	12.213328 sec.
Veddahs	8.927859 sec.
MN	25.674751 sec.
rinsing	13.431647 sec.
chugging	15.136422 sec.
Loftus_Road	6.840658 sec.
Goodison_Park	9.355585 sec.
Plainmoor	6.903479 sec.
kneading	14.838143 sec.
Molineux	9.215632 sec.
NQF	6.297355 sec.
OR	23.915851 sec.
reheating	15.002929 sec.
Ibrox	9.644248 sec.
Craven_Cottage	8.668745 sec.
preheating	15.927453 sec.
vulcanizing	15.490

Youth_Choirs	8.841136 sec.
Surrealist_Exhibition	10.041534 sec.
juried_exhibitions	8.916343 sec.
menageries	8.923989 sec.
tradeshows	7.141115 sec.
Biennials	15.833047 sec.
sculptural_installations	7.739975 sec.
trade_embargoes	6.628716 sec.
lectures_seminars	9.606380 sec.
moratoriums	7.219563 sec.
mania	20.782236 sec.
Palais_des	15.755177 sec.
Tretyakov_gallery	13.252447 sec.
financial_burdens	7.246925 sec.
meteor_shower	21.075613 sec.
biennales	10.178712 sec.
cognitive_bias	21.807955 sec.
Bookfair	14.398365 sec.
landed_aristocracy	7.991022 sec.
museums_galleries	12.645805 sec.
higher_echelons	8.700819 sec.
Triennal	15.353586 sec.
seminars_conferences	11.811316 sec.
voteless	8.956143 sec.
isolationist_stance	7.690675 sec.
Restrictions	12.199930 sec.
ultra_rightist	9.186552 sec.
understrength	9.816643 sec.
Huish	7.244217 sec.
Formby	7.439887 sec.
Islamic_extremist	8.862043 sec.
Eastwood	6.880029 sec.
Yardley	8.122653 sec.
untouchable	12.121238 sec.
unruly	14.054028 sec.
Ramsbottom	9.852

Cantrell	8.441292 sec.
Scruggs	9.320135 sec.
Womack	8.473098 sec.
Haney	8.759356 sec.
Blackmon	9.368593 sec.
without_hesitation	17.097974 sec.
Sayles	9.400328 sec.
Roberson	7.862616 sec.
fermentations	12.973670 sec.
cravings	15.102194 sec.
Ruffin	9.133499 sec.
Grier	7.842866 sec.
Suggs	9.839350 sec.
Dees	12.232772 sec.
Kravitz	8.598570 sec.
Lonzo	8.601206 sec.
Claypool	6.819183 sec.
Jaymes	8.568571 sec.
Burnette	8.573316 sec.
Combs	12.089708 sec.
infusions	16.758197 sec.
erucic_acid	15.494593 sec.
McDaniels	9.806777 sec.
Cotten	8.618568 sec.
Van_Zandt	7.264618 sec.
Brokaw	8.456754 sec.
Luckett	9.001062 sec.
LaRue	15.816553 sec.
Magness	8.888447 sec.
Troutman	9.691802 sec.
Sellers	14.960405 sec.
Ritch	14.869552 sec.
Dotson	8.376199 sec.
Durst	15.443741 sec.
Crutchfield	8.253669 sec.
186000 ego networks processed
Latimore	8.333309 sec.
Smitty	8.695061 sec.
Redman	8.704648 sec.
Cohan	7.283359 sec.
Kinky_Friedman	7.044775 sec.
Crowell	9.210710 sec.
Eubanks	9.328114 sec.
Prine	8.487635 sec.